In [1]:
#!/usr/bin/env python
# coding: utf-8
import os

from sklearn.model_selection import StratifiedKFold, train_test_split
from config import LSHS_DATAFILE, gpt_filtered_rephrase_lshs_file
import numpy as np
import time
import pandas as pd
from tqdm import tqdm

In [2]:
# import logging

# logging.basicConfig(
#     format='%(asctime)s %(levelname)-8s %(message)s',
#     level=logging.INFO,
#     datefmt='%Y-%m-%d %H:%M:%S')
# # The default levels are DEBUG, INFO, WARNING, ERROR, and CRITICAL.
# print(logging.WARNING)
# logging.getLogger()

In [3]:
import json
gpt_filtered_rephrase_tweets_file = gpt_filtered_rephrase_lshs_file

out_file = open(gpt_filtered_rephrase_tweets_file, "r")
filtered_rephrase_tweet_gpt = json.load(out_file)
out_file.close()

In [4]:
NUM_LABELS = 3
df = pd.read_csv(LSHS_DATAFILE)
domains = df['Domain'].unique().tolist()
for d in domains:
    print(d, df[df['Domain'] == d].shape)

Gender (9454, 4)
Religion (10869, 4)
Race (12013, 4)
Politics (11018, 4)
Sports (12306, 4)


In [5]:
# HateLabel	Final hate label decision 0-Normal, 1-Offensive, 2-Hate

# Setup for PyTorch-Lightning

In [6]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification, AutoConfig
from torch.utils.data import DataLoader, Dataset
import torchmetrics
import torch
import pytorch_lightning as pl

/home/atif/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2023-06-19 03:50:24.133289: I tensorflow/core/util/port.cc:110] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-06-19 03:50:24.166407: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-06-19 03:50:24.635702: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [7]:
os.environ["TOKENIZERS_PARALLELISM"] = "false"
# https://wandb.ai/jack-morris/david-vs-goliath/reports/Does-Model-Size-Matter-A-Comparison-of-BERT-and-DistilBERT--VmlldzoxMDUxNzU
MAX_EPOCHS = 5 #5
BATCH_SIZE = 16*2 #+ int(55 * 0.9*0.5)
LEARNING_RATE = 1e-5
# MODEL_LLM = 'distilbert-base-uncased'
MODEL_LLM = 'bert-base-uncased'

# Setting the seed
pl.seed_everything(42, workers=True)

Global seed set to 42


42

In [8]:
tokenizer = AutoTokenizer.from_pretrained(MODEL_LLM)
print("Tokenizer input max length:", tokenizer.model_max_length)
print("Tokenizer vocabulary size:", tokenizer.vocab_size)

Tokenizer input max length: 512
Tokenizer vocabulary size: 30522


In [9]:
class MyDataset(Dataset):
  def __init__(self, encodings, labels):
    self.encodings = encodings
    self.labels = labels

  def __getitem__(self, idx):
    '''
    encoding.items() -> 
      -> input_ids : [1,34, 32, 67,...]
      -> attention_mask : [1,1,1,1,1,....]
    '''
    item = {key:torch.tensor(val[idx]) for key, val in self.encodings.items()}
    item['labels'] = torch.tensor(self.labels[idx])
    return item

  def __len__(self):
    return len((self.labels))

In [10]:
class LightningModel(pl.LightningModule):
    def __init__(self, model_name_or_path, num_labels, learning_rate=LEARNING_RATE):
        super().__init__()

        self.learning_rate = learning_rate
        self.config = AutoConfig.from_pretrained(model_name_or_path, num_labels=num_labels)
        self.model = AutoModelForSequenceClassification.from_pretrained(model_name_or_path, config=self.config)

        # self.val_conf_mat = torchmetrics.ConfusionMatrix(task="multiclass", num_classes=NUM_LABELS)
        self.val_f1_macro_score = torchmetrics.classification.MulticlassF1Score(average="macro", num_classes=NUM_LABELS)
        self.val_f1_weighted_score = torchmetrics.classification.MulticlassF1Score(average="weighted", num_classes=NUM_LABELS)
        self.val_f1_non_avg_score = torchmetrics.classification.MulticlassF1Score(average="none", num_classes=NUM_LABELS)
        self.val_acc = torchmetrics.Accuracy(task="multiclass", num_classes=NUM_LABELS)
        
        # self.test_conf_mat = torchmetrics.ConfusionMatrix(task="multiclass", num_classes=NUM_LABELS)
        self.test_f1_macro_score = torchmetrics.classification.MulticlassF1Score(average="macro", num_classes=NUM_LABELS)
        self.test_f1_weighted_score = torchmetrics.classification.MulticlassF1Score(average="weighted", num_classes=NUM_LABELS)
        self.test_f1_non_avg_score = torchmetrics.classification.MulticlassF1Score(average="none", num_classes=NUM_LABELS)
        self.test_acc = torchmetrics.Accuracy(task="multiclass", num_classes=NUM_LABELS)
        
        self.metrics = {'val': [('val_f1_macro_score', self.val_f1_macro_score), ('val_f1_weighted_score', self.val_f1_weighted_score), ('val_acc', self.val_acc)],
                         'test': [('F1-Macro', self.test_f1_macro_score), ('F1-Weighted', self.test_f1_weighted_score),
                                  ('F1_Class 0', self.test_f1_non_avg_score.cpu()[0], 'test_f1_non_avg_score'), 
                                  ('F1_Class 1', self.test_f1_non_avg_score.cpu()[1], 'test_f1_non_avg_score'),
                                  ('F1_Class 2', self.test_f1_non_avg_score.cpu()[2], 'test_f1_non_avg_score'),
                                  ('Accuracy', self.test_acc)
                                 ]
                        }
        

    def forward(self, input_ids, attention_mask, labels):
        return self.model(input_ids, attention_mask=attention_mask, labels=labels)
        
    def training_step(self, batch, batch_idx):
        outputs = self(batch["input_ids"], attention_mask=batch["attention_mask"],
                       labels=batch["labels"])        
        self.log("train_loss", outputs["loss"])
        return outputs["loss"]  # this is passed to the optimizer for training

    def echo_metrics(self, key, predicted_labels, batch_labels):
        for itm in self.metrics[key]:
            if len(itm) == 2:
                mt_str, met = itm
                metric_attribute = None
            else:
                mt_str, met, metric_attribute = itm
                # print('this', mt_str, met, metric_attribute)
            met(predicted_labels, batch_labels)
            self.log(mt_str, met, prog_bar=True, metric_attribute=metric_attribute)
        
        
    
    def validation_step(self, batch, batch_idx):
        outputs = self(batch["input_ids"], attention_mask=batch["attention_mask"],
                       labels=batch["labels"])        
        self.log("val_loss", outputs["loss"], prog_bar=True)
        
        logits = outputs["logits"]
        predicted_labels = torch.argmax(logits, 1)

        self.echo_metrics('val', predicted_labels, batch["labels"])
        # print('#n here->',self.val_f1_non_avg_score(predicted_labels, batch["labels"]).cpu()[0])
        
        
    def test_step(self, batch, batch_idx):
        outputs = self(batch["input_ids"], attention_mask=batch["attention_mask"],
                       labels=batch["labels"])        
        
        logits = outputs["logits"]
        predicted_labels = torch.argmax(logits, 1)
        self.echo_metrics('test', predicted_labels, batch["labels"])

    def configure_optimizers(self):
        optimizer = torch.optim.Adam(self.parameters(), lr=self.learning_rate)
        return optimizer

# Experiment

In [11]:
CF_LABEL = 0
import random
random.seed(42)

In [12]:
print(df['Label'].value_counts())
problematic_df = df[df['Label']>0]
problematic_df.shape

Label
0    44874
1     9669
2     1117
Name: count, dtype: int64


(10786, 4)

In [13]:
def get_tweets():
    gpt_counterfactual_tweets = {}
    tot = problematic_df.shape[0]
    # print(tot)
    for i in range(0, tot):
        idx = problematic_df.iloc[i].name
        if str(i) in filtered_rephrase_tweet_gpt:
            gpt_counterfactual_tweets[idx] = filtered_rephrase_tweet_gpt[str(i)]
    return gpt_counterfactual_tweets
    
gpt_counterfactual_tweets = get_tweets()

In [14]:
import config
from nltk.tokenize import TweetTokenizer
import mosestokenizer
import numpy as np

def get_offensive_words():
    _df = pd.read_csv(config.en_swear_words_datafile, index_col=0)
    
    s = np.logical_or(_df['Level of offensiveness']=='Strongest words', _df['Level of offensiveness']=='Strong words')
    # display(_df[s]['Word'].to_list())
    wd_list = _df['Word'].to_list()
    
    _df = pd.read_csv(config.en_profanity_datafile, index_col=None)
    s = _df['severity_description'] == 'Severe'
    # wd_list.extend(_df[s]['text'].to_list())
    wd_list.extend(_df['text'].to_list())
    wd_list = set(map(str.lower, wd_list))
    return wd_list

offensive_wd_list = get_offensive_words()

In [15]:
def find_phrases(tokens, phrases):
    tokens = list(map(str.lower, tokens))
    """
    Find phrases in a list of sequential tokens.
    
    Args:
        tokens (list): List of sequential tokens.
        phrases (list): List of phrases to search for.
        
    Returns:
        A list of tuples containing the start and end index of each found phrase.
    """
    found_phrases = []
    
    for i in range(len(tokens)):
        for phrase in phrases:
            if tokens[i:i+len(phrase)] == phrase:
                found_phrases.append((i, i+len(phrase)-1))
    
    return found_phrases

def offensive_lexicon_used(t):
    tk = TweetTokenizer()
    detk = mosestokenizer.MosesDetokenizer('en')
    tk = tk.tokenize(t)
    # print(tk)
    phrase_index = find_phrases(tk, list(map(str.split, offensive_wd_list)))
    return len(phrase_index)

In [16]:
def get_counterfactual_tweets(data, labels, cf_label, single_cf_per_tweet=False, cf_size_prop_to_data=1.0, only_tweets_with_offensive_lexicon=True):
    tweets = []
    cnt =0 
    for idx in data.index:
        if idx in gpt_counterfactual_tweets:
            if (not only_tweets_with_offensive_lexicon) or offensive_lexicon_used(X[idx]):
                cnt += 1
                if not single_cf_per_tweet:
                    tweets.extend(gpt_counterfactual_tweets[idx])
                else:
                    tweets.append(gpt_counterfactual_tweets[idx][0])
    print('> Total Tweets used to generate counterfactuals ' + str(cnt))
    print('> Total counterfactuals added ' + str(len(tweets)))
    k = round(cf_size_prop_to_data * len(tweets))
    
    tweets = random.sample(tweets, k=k)
    print('> Counterfactual size ' + str(k) + ' at rate ' + str(cf_size_prop_to_data))
    cf_target = k*[cf_label]
    return pd.concat([data, pd.Series(tweets)], axis=0), pd.concat([labels, pd.Series(cf_target)], axis=0)

In [17]:
only_tweets_with_offensive_lexicon = False

In [18]:
for d in domains:
    sel_df = df[df['Domain'] == d]
    print(d, sel_df.shape)
    X, y = sel_df['Tweet'], sel_df['Label'].astype(int)
    skf = StratifiedKFold(n_splits=2, random_state=None)
    for splt_idx, (train_index , test_index) in enumerate(skf.split(X, y)):
        print(splt_idx)
        X_train , X_test = X.iloc[train_index], X.iloc[test_index]
        y_train , y_test = y.iloc[train_index] , y.iloc[train_index]
        _,_ = get_counterfactual_tweets(
                X_train, y_train, cf_label=CF_LABEL, single_cf_per_tweet=True, cf_size_prop_to_data=.1, only_tweets_with_offensive_lexicon=only_tweets_with_offensive_lexicon)

Gender (9454, 4)
0
> Total Tweets used to generate counterfactuals 845
> Total counterfactuals added 845
> Counterfactual size 84 at rate 0.1
1
> Total Tweets used to generate counterfactuals 767
> Total counterfactuals added 767
> Counterfactual size 77 at rate 0.1
Religion (10869, 4)
0
> Total Tweets used to generate counterfactuals 762
> Total counterfactuals added 762
> Counterfactual size 76 at rate 0.1
1
> Total Tweets used to generate counterfactuals 771
> Total counterfactuals added 771
> Counterfactual size 77 at rate 0.1
Race (12013, 4)
0
> Total Tweets used to generate counterfactuals 570
> Total counterfactuals added 570
> Counterfactual size 57 at rate 0.1
1
> Total Tweets used to generate counterfactuals 520
> Total counterfactuals added 520
> Counterfactual size 52 at rate 0.1
Politics (11018, 4)
0
> Total Tweets used to generate counterfactuals 1001
> Total counterfactuals added 1001
> Counterfactual size 100 at rate 0.1
1
> Total Tweets used to generate counterfactuals

In [19]:
def __exp__(train_texts, train_labels, valid_texts, valid_labels, test_texts, test_labels, CF=False):
   
    if not CF:
        print('> Train samples', len(train_texts))
    else:
        print('> Train with CF samples', len(train_texts))
    
    
    train_encodings = tokenizer(list(train_texts), truncation = True, padding = True)
    valid_encodings = tokenizer(list(valid_texts), truncation = True, padding = True)
    test_encodings = tokenizer(list(test_texts), truncation = True, padding = True)

    #datasets
    train_dataset = MyDataset(train_encodings, train_labels)
    valid_dataset = MyDataset(valid_encodings, valid_labels)
    test_dataset = MyDataset(test_encodings, test_labels)
    
    #dataloaders
    bs = BATCH_SIZE
    train_loader = DataLoader(train_dataset, batch_size = bs, shuffle = True, num_workers=4)
    valid_loader = DataLoader(valid_dataset, batch_size = bs, shuffle = True, num_workers=4)
    test_loader = DataLoader(test_dataset, batch_size = bs, shuffle = True, num_workers=4)
    print(len(train_loader), len(valid_loader))

    # Setting the seed
    pl.seed_everything(42, workers=True)
    lightning_model = LightningModel(MODEL_LLM, NUM_LABELS)

    trainer = pl.Trainer(
        max_epochs=MAX_EPOCHS,
        accelerator="gpu",
        devices=1,
        deterministic=True,
        # log_every_n_steps=30,
        enable_checkpointing=True,  
        logger=False
    )
    
    trainer.fit(model=lightning_model,
                train_dataloaders=train_loader,
                val_dataloaders=valid_loader)
    
    r = trainer.test(lightning_model, dataloaders=test_loader, ckpt_path="best")
    del lightning_model
    del trainer
    return r



In [20]:
def get_splits(_X, _y, test_val_split=0.5):
    skf = StratifiedKFold(n_splits=n_splits, random_state=None)

    for splt_idx, (train_index , test_index) in enumerate(skf.split(_X, _y)):
        x_train , x_test = _X.iloc[train_index], _X.iloc[test_index]
        y_train , y_test = _y.iloc[train_index] , _y.iloc[test_index]
    
        x_val, x_test, y_val, y_test = \
                    train_test_split(x_test, y_test, test_size=test_val_split) 

        train_texts = x_train.values
        train_labels = y_train.values
        
        valid_texts = x_val.values
        valid_labels = y_val.values
        
        test_texts = x_test.values
        test_labels = y_test.values
        yield splt_idx, (x_train, y_train, train_texts, train_labels, valid_texts, valid_labels, test_texts, test_labels)

def run_experiment_org(_X, _y, n_splits=2):
    out_lst = []
    for splt_idx, data_item in get_splits(_X, _y):
        # print(splt_idx)
        x_train, y_train, train_texts, train_labels, valid_texts, valid_labels, test_texts, test_labels = data_item

        org = __exp__(train_texts, train_labels, valid_texts, valid_labels, test_texts, test_labels, CF=False)

        l = [('splt_idx', splt_idx, len(test_labels)),  ('train', len(train_labels)), {'Org': org}]
        out_lst.append(l)
    return out_lst

def run_experiment_counter_factuals(_X, _y, n_splits=2, cf_size_prop_to_data=0.1):
    out_lst = []
    for splt_idx, data_item in get_splits(_X, _y):
        # print(splt_idx)
        x_train, y_train, train_texts, train_labels, valid_texts, valid_labels, test_texts, test_labels = data_item

        x_train_with_cf, y_training_with_cf = get_counterfactual_tweets(
            x_train, y_train, cf_label=CF_LABEL, single_cf_per_tweet=True, cf_size_prop_to_data=cf_size_prop_to_data, only_tweets_with_offensive_lexicon=only_tweets_with_offensive_lexicon)
        train_texts_cf = x_train_with_cf.values
        train_labels_cf = y_training_with_cf.values

        cf = __exp__(train_texts_cf, train_labels_cf, valid_texts, valid_labels, test_texts, test_labels, CF=True)
        l = [('splt_idx', splt_idx, len(test_labels)),  ('train', len(y_training_with_cf)), {'CF': cf}]
        out_lst.append(l)
    return out_lst

In [21]:
n_splits=5
cf_size_prop_to_data_lst = list(np.arange(0.1, 1.1, 0.1))
# n_splits=2
# cf_size_prop_to_data_lst = list(np.arange(0.1, 0.2, 0.1))
try:
    del X, y
except:
    pass

In [22]:
def run_now():
    complete_result = []
    out_dict = {}
    for d in domains:
        out_dict[d] = {}
        sel_df = df[df['Domain'] == d]
        print(d, sel_df.shape)
        X, y = sel_df['Tweet'], sel_df['Label'].astype(int)
        
        res_bert_lst = run_experiment_org(X, y, n_splits=n_splits)
        out_dict[d]['Org'] = res_bert_lst
        out_dict[d]['CF'] = {}
        for cf_size_prop_to_data in cf_size_prop_to_data_lst:
            res_bert_lst = run_experiment_counter_factuals(X, y, n_splits=n_splits, cf_size_prop_to_data=cf_size_prop_to_data)
            out_dict[d]['CF'][cf_size_prop_to_data] = res_bert_lst
        complete_result.append(out_dict)
        json.dump(out_dict, open('out/'+ MODEL_LLM + '-EP_'+ str(MAX_EPOCHS) + '-ft-lshd22.json', 'w'))
    return complete_result

start = time.time()
complete_result = run_now()
end = time.time()
elapsed = end - start
print(f"Time elapsed {elapsed/60:.2f} min")

Gender (9454, 4)
> Train samples 7563


Global seed set to 42


237 30


Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

Sanity Checking: 0it [00:00, ?it/s]

...

Epoch 0: 100%|████████████████████████████████| 356/356 [01:54<00:00,  3.11it/s]
Validation: 0it [00:00, ?it/s]
Validation DataLoader 0:  97%|█████████████████▌| 38/39 [00:02<00:00, 17.34it/s]
Epoch 0: 100%|█| 356/356 [01:57<00:00,  3.04it/s, val_loss=0.316, val_f1_macro_s
Epoch 1: 100%|█| 356/356 [01:54<00:00,  3.10it/s, val_loss=0.316, val_f1_macro_s
Validation: 0it [00:00, ?it/s]
Validation DataLoader 0:  97%|█████████████████▌| 38/39 [00:02<00:00, 17.34it/s]
Epoch 1: 100%|█| 356/356 [01:57<00:00,  3.03it/s, val_loss=0.292, val_f1_macro_s
Epoch 2: 100%|█| 356/356 [01:54<00:00,  3.10it/s, val_loss=0.292, val_f1_macro_s
Validation: 0it [00:00, ?it/s]
Validation DataLoader 0:  97%|█████████████████▌| 38/39 [00:02<00:00, 17.35it/s]
Epoch 2: 100%|█| 356/356 [01:57<00:00,  3.03it/s, val_loss=0.263, val_f1_macro_s
Epoch 3: 100%|█| 356/356 [01:54<00:00,  3.10it/s, val_loss=0.263, val_f1_macro_s
Validation: 0it [00:00, ?it/s]
Validation DataLoader 0:  97%|█████████████████▌| 38/39 [00:02<00:

`Trainer.fit` stopped: `max_epochs=5` reached.


Epoch 4: 100%|█| 356/356 [01:59<00:00,  2.98it/s, val_loss=0.377, val_f1_macro_s


You are using a CUDA device ('NVIDIA GeForce RTX 3080') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_precision('medium' | 'high')` which will trade-off precision for performance. For more details, read https://pytorch.org/docs/stable/generated/torch.set_float32_matmul_precision.html#torch.set_float32_matmul_precision
Restoring states from the checkpoint path at /home/atif/work/notebook-data/chatgpt/checkpoints/epoch=4-step=1780.ckpt
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Loaded model weights from the checkpoint at /home/atif/work/notebook-data/chatgpt/checkpoints/epoch=4-step=1780.ckpt
/home/atif/.local/lib/python3.10/site-packages/pytorch_lightning/trainer/connectors/data_connector.py:478: PossibleUserWarning: Your `test_dataloader`'s sampler has shuffling enabled, it is strongly recommended that you turn shuffling off for val/test dataloaders.
  rank_zero_warn(


Testing DataLoader 0: 100%|█████████████████████| 39/39 [00:02<00:00, 15.05it/s]
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
        Accuracy            0.9008935689926147
        F1-Macro            0.6873461008071899
       F1-Weighted          0.9047609567642212
       F1_Class 0           0.9421841502189636
       F1_Class 1           0.8087431788444519
       F1_Class 2           0.31111112236976624
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
Time elapsed 1668.32 min


In [23]:
complete_result

[{'Gender': {'Org': [[('splt_idx', 0, 946),
     ('train', 7563),
     {'Org': [{'F1-Macro': 0.7387224435806274,
        'F1-Weighted': 0.9135377407073975,
        'F1_Class 0': 0.949999988079071,
        'F1_Class 1': 0.833734929561615,
        'F1_Class 2': 0.4324324429035187,
        'Accuracy': 0.9143763184547424}]}],
    [('splt_idx', 1, 946),
     ('train', 7563),
     {'Org': [{'F1-Macro': 0.7776308059692383,
        'F1-Weighted': 0.936324417591095,
        'F1_Class 0': 0.9613559246063232,
        'F1_Class 1': 0.8715365529060364,
        'F1_Class 2': 0.5,
        'Accuracy': 0.937632143497467}]}],
    [('splt_idx', 2, 946),
     ('train', 7563),
     {'Org': [{'F1-Macro': 0.8429104089736938,
        'F1-Weighted': 0.9529786705970764,
        'F1_Class 0': 0.9722991585731506,
        'F1_Class 1': 0.9112709760665894,
        'F1_Class 2': 0.6451612710952759,
        'Accuracy': 0.9534883499145508}]}],
    [('splt_idx', 3, 946),
     ('train', 7563),
     {'Org': [{'F1-Macro':

In [24]:
# Gender, Religion, Race, *Politics, Sports
# change MAX_EPOCH, CF, n_splits --> dummy small exp

In [25]:
# [{'Accuracy': 0.9230769276618958,
#   'F1-Macro': 0.3199999928474426,
#   'F1-Weighted': 0.8861538171768188,
#   'F1_Class 0': 0.0,
#   'F1_Class 1': 0.9599999785423279,
#   'F1_Class 2': 0.0}]